<a href="https://colab.research.google.com/github/guantao21/AlgerMusicPlayer/blob/main/ChatTTS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## 简介

ChatTTS是一款专为对话场景设计的语音生成模型，适用于AI助手对话、对话语音和视频介绍，支持中英文。它优化了对话任务，实现自然流畅的多说话人语音合成，并能控制细粒度的韵律特征，如笑声、停顿和插入词。ChatTTS在韵律方面表现卓越，提供预训练模型，支持进一步研究。  

开源项目地址[GitHub](https://github.com/2noise/ChatTTS)  
使用方法和本地运行 [博客](https://www.tonyisstark.com/)

## 克隆源码并安装

In [1]:
!git clone https://github.com/2noise/ChatTTS.git
!git checkout 8b2bd819324d7def592fee4c7c19805038525aca
%cd /content/ChatTTS
!pip install -r requirements.txt

Cloning into 'ChatTTS'...
remote: Enumerating objects: 2767, done.
remote: Counting objects: 100% (780/780), done.
remote: Compressing objects: 100% (351/351), done.
remote: Total 2767 (delta 536), reused 429 (delta 429), pack-reused 1987 (from 4)
Receiving objects: 100% (2767/2767), 10.42 MiB | 29.97 MiB/s, done.
Resolving deltas: 100% (1660/1660), done.
fatal: not a git repository (or any of the parent directories): .git
/content/ChatTTS
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 627.6/627.6 kB 16.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 104.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of wetextprocessing to determine which version is compatible with other requirements. This could take a while.
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
INFO: pip is looking at m

## 加载模型

In [ ]:
import torch
torch._dynamo.config.cache_size_limit = 64
torch._dynamo.config.suppress_errors = True
torch.set_float32_matmul_precision('high')

import ChatTTS
from IPython.display import Audio

chat = ChatTTS.Chat()
chat.load_models()

# Use force_redownload=True if the weights updated.
# chat.load_models(force_redownload=True)

# If you download the weights manually, set source='locals'.
# chat.load_models(source='local', local_path='YOUR LOCAL PATH')

## 运行推理

### 批量生成

In [ ]:
texts = ["So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with.",]*3 \
        + ["我觉得像我们这些写程序的人，他，我觉得多多少少可能会对开源有一种情怀在吧我觉得开源是一个很好的形式。现在其实最先进的技术掌握在一些公司的手里的话，就他们并不会轻易的开放给所有的人用。"]*3

wavs = chat.infer(texts)

In [ ]:
Audio(wavs[0], rate=24_000, autoplay=True)

In [ ]:
Audio(wavs[3], rate=24_000, autoplay=True)

### 自定义参数

In [ ]:
params_infer_code = {'prompt':'[speed_5]', 'temperature':.3}
params_refine_text = {'prompt':'[oral_2][laugh_0][break_6]'}

wav = chat.infer('四川美食可多了，有麻辣火锅、宫保鸡丁、麻婆豆腐、担担面、回锅肉、夫妻肺片等，每样都让人垂涎三尺。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)

### 随机的说话人

In [ ]:
rand_spk = chat.sample_random_speaker()
params_infer_code = {'spk_emb' : rand_spk, }

wav = chat.infer('四川美食确实以辣闻名，但也有不辣的选择。比如甜水面、赖汤圆、蛋烘糕、叶儿粑等，这些小吃口味温和，甜而不腻，也很受欢迎。', \
    params_refine_text=params_refine_text, params_infer_code=params_infer_code)

 25%|██▌       | 513/2048 [00:15<00:45, 33.90it/s]


In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)

### 两步走

In [ ]:
text = "So we found being competitive and collaborative was a huge way of staying motivated towards our goals, so one person to call when you fall off, one person who gets you back on then one person to actually do the activity with."
chat.infer(text, refine_text_only=True)

In [ ]:
text = 'so we found being competitive and collaborative [uv_break] was a huge way of staying [uv_break] motivated towards our goals, [uv_break] so [uv_break] one person to call [uv_break] when you fall off, [uv_break] one person who [uv_break] gets you back [uv_break] on then [uv_break] one person [uv_break] to actually do the activity with.'
wav = chat.infer(text, skip_refine_text=True)

In [ ]:
Audio(wav[0], rate=24_000, autoplay=True)